<a href="https://colab.research.google.com/github/penelopetir/BIOL74-Final-Project/blob/main/Final_Project_Passive_Properties.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Before starting, we'll install neuron in our current runtime as usual.

In [ ]:
%pip install neuron # only need to run this cell once to install
                    # neuron in the local jupyter environment

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 15.0/15.0 MB 20.6 MB/s eta 0:00:00


Run the code block below just once to get all the files from the repository into our colab session and compile the MOD mechanism files we'll be using

In [ ]:
repo_name = 'BIOL74-Final-Project'
if 'google.colab' in str(get_ipython()):
    import os
    if not os.path.exists(repo_name):
        !git clone https://github.com/penelopetir/{repo_name}.git # downloads repository into our Google colab session's file system

    os.chdir(repo_name) # Changing working directory to downloaded repository

# Compile mechanisms
!nrnivmodl mechanisms

Cloning into 'BIOL74-Final-Project'...
remote: Enumerating objects: 406, done.
remote: Counting objects: 100% (224/224), done.
remote: Compressing objects: 100% (131/131), done.
remote: Total 406 (delta 135), reused 161 (delta 91), pack-reused 182
Receiving objects: 100% (406/406), 1.29 MiB | 4.52 MiB/s, done.
Resolving deltas: 100% (228/228), done.
/content/BIOL74-Final-Project
Mod files: "mechanisms/mechanisms/CadepK.mod" "mechanisms/mechanisms/Ca.mod"

Creating 'x86_64' directory for .o files.

 -> Compiling mod_func.cpp
 -> NMODL ../mechanisms/CadepK.mod
 -> NMODL ../mechanisms/Ca.mod
Translating CadepK.mod into /content/BIOL74-Final-Project/x86_64/CadepK.c
Translating Ca.mod into /content/BIOL74-Final-Project/x86_64/Ca.c
Thread Safe
Thread Safe
 -> Compiling CadepK.c
 -> Compiling Ca.c
 => LINKING shared library ./libnrnmech.so
 => LINKING executable ./special LDFLAGS are:    -pthread
Successfully created x86_64/special


## Introduction
For this exercise, we'll be adapting a model of a L5PC to model granule neurons traced from wild type and PTEN KO groups


Start by importing the packages we'll be using.

In [ ]:
from neuron import h # all NEURON hoc functions are accessed through h
from neuron import gui # if you're running this notebook in a local environment (instead of on google colab), launches the GUI
h.load_file('stdrun.hoc') # loads neuron standard hoc library, not always necessary
import numpy as np
import matplotlib as mpl
mpl.rcParams['axes.spines.right'] = False
mpl.rcParams['axes.spines.top'] = False
import matplotlib.pyplot as plt
import plotly
from plotly.subplots import make_subplots
import plotly.graph_objects as go

if 'google.colab' in str(get_ipython()): # For making interactive plots work on google colab
    from google.colab import output
    output.enable_custom_widget_manager()
else:
    plotly.offline.init_notebook_mode() # for printing notebooks offline

#Importing Morphologies

Files from the github of traced neurons from NeuroLuicda 360 are imported and created with proper morphology. Biophysics are modeled after the Aradi et al 1999 paper.

In [ ]:
from helper_functions import createGranuleCell

genotype = "WT" #change this string to "WT" or "KO" to determine which neuron to run the following code on

if genotype == "WT":
  WT_file = "morphologies/WT.asc" # morphology file
  GC = createGranuleCell(WT_file, "passive")
elif genotype == "KO":
  KO_file = "morphologies/PTEN_KO.asc" # morphology file
  GC = createGranuleCell(KO_file, "passive")
else:
  print("No neuron found")

# Create recording vectors for time and somatic voltage
t_vec = h.Vector().record(h._ref_t)
v_soma = h.Vector().record(GC.soma[0](0.5)._ref_v)

In [ ]:
#probing neurons for their parameters
print(f"{genotype} Soma Ra: {GC.soma[0].Ra} MOhm")
print(f"{genotype} Soma L: {GC.soma[0].L:.2f} um")
print(f"{genotype} Soma Diameter: {GC.soma[0].diam:.2f} um")
print(f"{genotype} Soma Cm: {GC.soma[0].cm} pF")
print(f"{genotype} Soma Rm: {1/GC.soma[0](0.5).pas.g} MOhm")
print(f"{genotype} Soma erev: {GC.soma[0](0.5).pas.e} mV")

WT Soma Ra: 210.0 MOhm
WT Soma L: 9.36 um
WT Soma Diameter: 4.86 um
WT Soma Cm: 1.0 pF
WT Soma Rm: 40000.0 MOhm
WT Soma erev: -70.0 mV


In [ ]:
h.topology()


|-|       passivetemplate[0].soma[0](0-1)
  `|       passivetemplate[0].apic[0](0-1)
    `|       passivetemplate[0].apic[1](0-1)
      `--|       passivetemplate[0].apic[2](0-1)
          `--|       passivetemplate[0].apic[3](0-1)
          `--|       passivetemplate[0].apic[4](0-1)
      `|       passivetemplate[0].apic[5](0-1)
        `----|       passivetemplate[0].apic[6](0-1)
        `------|       passivetemplate[0].apic[7](0-1)
    `|       passivetemplate[0].apic[8](0-1)
      `--|       passivetemplate[0].apic[9](0-1)
          `|       passivetemplate[0].apic[10](0-1)
            `--|       passivetemplate[0].apic[11](0-1)
            `--|       passivetemplate[0].apic[12](0-1)
          `----|       passivetemplate[0].apic[13](0-1)
      `|       passivetemplate[0].apic[14](0-1)
        `----|       passivetemplate[0].apic[15](0-1)
        `|       passivetemplate[0].apic[16](0-1)
          `------|       passivetemplate[0].apic[17](0-1)
          `------|       passivetem

1.0

#Measuring Rin and Cm
In this next section, we will be calibrating our model in an attempt to match the Williams et al 2015 paper results. The objective is to get our values of Rm and Cm to be as such:

Control: 10pF, 600 M$\Omega$

PTEN KO: 40pF, 250 M$\Omega$

The approach we will be taking is to apply a current stimulus and then measure the change in voltage of the soma membrane. With this, we can use Ohm's law to calculate the resistance by dividing the change in voltage by the current.

From here, we can take this value and then fit the decay time to a first-order exponential curve to calculate tau. From there, we can divide tau by Rin to get the capacitance value.

In [ ]:
#creating current clamp
iclamp = h.IClamp(GC.soma[0](0.5))

#generating a recording vector for current
Ic = h.Vector().record(iclamp._ref_i)

In [ ]:
def run_and_plot_Iclamp_sim(t,v,ic):
    h.run()
    # Plot results
    fig = make_subplots(rows=2,cols=1)
    # voltage
    fig.add_trace(go.Scatter(x=t,y=v,showlegend=False),row=1,col=1)
    fig['layout']['yaxis']['title']='Vm (mV)'
    # Current
    fig.add_trace(go.Scatter(x=t,y=ic,showlegend=False),row=2,col=1)
    fig['layout']['xaxis2']['title']='time (ms)'
    fig['layout']['yaxis2']['title']='Ic (nA)'
    fig.show()

In [ ]:
#running the current simulation
#setting parameters for the current clamp
iclamp.amp = 0.005 #nA
iclamp.dur = 500 #ms
iclamp.delay = 5 #ms

h.v_init = -70 # mV - initial voltage of the model system
h.dt = 0.1  # ms - time step
h.celsius = 37 # degrees celsius - ephys recordings at this temp
h.tstop = 1000 # ms - simulation duration

run_and_plot_Iclamp_sim(t_vec, v_soma, Ic)

Changed dt


In [ ]:
#helper function to find the index of the occurence of a value (num) in an array
def find_index(num, vector):
  diff = [np.abs(element - num) for element in np.array(vector)]
  return np.argmin(diff)

#function used to calculate the passive properties of the soma
def calc_passive(v_soma, amp):
  v_min = np.min(np.array(v_soma))
  v_max = np.max(np.array(v_soma))

  Rin = np.abs((v_max - v_min)/(amp)) #mV/nA = MOhms

  v_soma_vec = np.array(v_soma)
  fall_start = find_index(v_max, v_soma_vec) #finds the index of the max voltage
  fall = v_soma_vec[fall_start:] #slices array so we only have the fall data
  t_init = t_vec[fall_start] #time at the minimum voltage, the start of the fall

  exp_decay = [0.633, 0.865, 0.95]
  tau = []
  for i, factor in enumerate(exp_decay):
    decay_to = v_max - factor*(v_max-v_min) #value to decay to from v_max
    t_val = t_vec[fall_start+find_index(decay_to, fall)]
    t_diff = t_val - t_init
    tau.append(t_diff/(i+1))

  ave_tau = np.mean(tau)
  cap = 1e3*ave_tau/Rin #to make it into pF from nF

  return Rin, cap, ave_tau

In [ ]:
Rin, cap, ave_tau = calc_passive(v_soma, iclamp.amp)
print(f"Rin = {Rin:.2f} MOhm")
print(f"Capacitance: {cap:.2f}pF")
print(f"Tau: {ave_tau:.2f} ms")

Rin = 737.67 MOhm
Capacitance: 71.94pF
Tau: 53.07 ms


## Changing Parameters

Now that we know our neuron's starting point, we need to try to get it to fit the model's capacitance and input resistances.

Control: 10pF, 600 M$\Omega$

PTEN KO: 40pF, 250 M$\Omega$

In [ ]:
#running the current simulation
#setting parameters for the current clamp
iclamp.amp = 0.01 #nA
iclamp.dur = 500 #ms
iclamp.delay = 5 #ms

h.v_init = -70 # mV - initial voltage of the model system
h.dt = 0.1  # ms - time step
h.celsius = 37 # degrees celsius - ephys recordings at this temp
h.tstop = 1000 # ms - simulation duration

GC.soma[0](0.5).pas.g = 2.5e-5
GC.soma[0].diam = 5e-5
GC.soma[0].L = 1

run_and_plot_Iclamp_sim(t_vec, v_soma, Ic)
Rin, cap, tau = calc_passive(v_soma, iclamp.amp)
print(f"Rin: {Rin}")
print(f"Cap: {cap}")
print(f"Tau: {tau}")

Changed dt


Rin: 767.4750176642015
Cap: 69.67834477768218
Tau: 53.47638888906395
